### Libs & Data

In [1]:
import numpy as np
import pandas as pd
import os
import re
import nltk

from transformers import BartTokenizer, BartForConditionalGeneration, BartConfig
from transformers import pipeline
from sentence_transformers import SentenceTransformer

import torch
import umap
import hdbscan
from sklearn.feature_extraction.text import CountVectorizer

import matplotlib.pyplot as plt

In [8]:
df = pd.read_csv("data/data_sum.csv")
df.shape

(23769, 7)

In [9]:
df.head()

title         author  \
0      A snapshot of multiculturalism in South Korea  Lee Sun-young   
1                   [Weekender] Korea’s dynamic 2017    Choi He-suk   
2  People's Party members support Ahn's push for ...         Yonhap   
3  [Newsmaker] Panamanian vessel probed over susp...         Yonhap   
4  Hong Kong ship crew questioned in S. Korea for...            AFP   

                  time                                        description  \
0  2018-01-01 17:07:00  With birthrates persistently low and the senio...   
1  2018-01-01 13:22:00  From North Korea’s nuclear weapons program nea...   
2  2017-12-31 16:18:00  The leader of the center-left People's Party g...   
3  2017-12-31 14:55:00  PYEONGTAEK  -- South Korea has seized and insp...   
4  2017-12-30 15:44:00  The crew of a Hong Kong-registered ship have b...   

                                                body         section  \
0  With birthrates persistently low and the senio...  Social affairs   
1  From North Korea’s nuclear weapons program nea...  Social affairs   
2  The leader of the center-left People's Party g...        Politics   
3  PYEONGTAEK  -- South Korea has seized and insp...     North Korea   
4  The crew of a Hong Kong-registered ship have b...     North Korea   

                                     summarized_body  
0  As of 2016, more than 2 million foreign nation...  
1  The corruption scandal that broke out in 2016 ...  
2  Ahn Cheol-soo, leader of the center-left Peopl...  
3  The 5,100-ton KOTI is being held in the wester...  
4  The crew of a Hong Kong-registered ship have b...

**Embedding**

In [8]:
device = "cuda:0" if torch.cuda.is_available() else "cpu"
model = SentenceTransformer('distilbert-base-nli-mean-tokens').to(device)

Downloading:   0%|          | 0.00/690 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/3.99k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/550 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/122 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/229 [00:00<?, ?B/s]

...

Downloading:   0%|          | 0.00/112 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/466k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/450 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/232k [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/190 [00:00<?, ?B/s]

In [10]:
df['embeddings'] = df['summarized_body'].map(lambda x: model.encode(x, show_progress_bar=True))

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [11]:
df.to_csv("embed", index=False)

**Clustering**

In [ ]:
%% time
# UMAP
n_neighbors = 15
n_dim = 30

# df['umap'] = df['embeddings'].map(lambda x: umap.UMAP(n_neighbors=n_neighbors, 
#                                                       n_components=n_dim, 
#                                                       metric='cosine').fit_transform(x))

umap.UMAP(n_neighbors=n_neighbors, n_components=n_dim, metric='cosine').fit_transform(df['embeddings'][0])

In [ ]:
# HDBSCAN
